# The pooling problem

In the pooling problem, source materials with are mixed in intermediate pools to create a number of output products. The output products are constrained by the quality of a certain attribute. In this notebook, we consider the small pooling example of Haverly:

C. A. Haverly, *Studies of the behavior of the recursion for the pooling problem*, SIGMAP Bulletin, 25 (1978), pp. 19–28. [pdf](https://www.eq.uc.pt/~nuno/eps/Edicoes_anteriores/2012-13/aula08/Haverly%20(1978).pdf)

In this example, there are three sources of oil, each of which contains a different percentage of sulfur. Given the pooling layout, these materials are to be blended in such a way to create two separate oil products. These final products have requirements on the percentage of sulfur they can contain, as well as how much of the product can be produced.

The problem's difficulty stems from the fact that it is a non-convex problem, as some of the constraints contain bilinear terms. Gurobi introduced support for non-convex quadratically constrained models with release 9.0. This notebook demonstrates how the example pooling problem can be defined, modeled, and solved with Gurobi/Python.

Most nonlinear solvers look for a local solution to this problem. In contrast, Gurobi finds the global optimum.

We begin by importing the `gurobipy` package.

In [ ]:
from gurobipy import *

## Define data

Now, we define the data used in Haverly's 1978 paper.

In [ ]:
# Define the crude oil sources, cost per unit, and sulfur percentage (i.e., quality)
sources, costs, sulfur = multidict({ 
    "A" : [  6, 3 ],
    "B" : [ 16, 1 ],
    "C" : [ 10, 2 ] 
})

# Define the crude oil sinks, market price, maximum sulfur percentage (quality), and maximum satisfiable demand
sinks, price, max_sulfur, demand = multidict({
    "X" : [  9, 2.5, 100 ],
    "Y" : [ 15, 1.5, 200 ]
})

# Define intermediate pools
pools = [ "P" ]

# Node connections (i.e., graph edges)
connections = tuplelist([
    ("A", "P"), ("B", "P"),  # Connections to pool
    ("P", "X"), ("P", "Y"),  # Connections from pool to sink
    ("C", "X"), ("C", "Y")   # Direct connections
])

## Visualizing the problem

We can draw the directed graph with the `graphviz` package (see [here](https://graphviz.readthedocs.io/en/stable/manual.html)).

In [ ]:
from graphviz import Digraph
dot = Digraph(graph_attr={'rankdir': 'LR'}, node_attr={'fontcolor':'blue', 'shape' : 'box'})
for pool in pools:
    dot.node(pool, shape='doublecircle')
for sink in sinks:
    dot.node(sink, "{:s} @${:d}\n\u2264 {:0.1f}%\n \u2264 {:d}".format(sink, price[sink], max_sulfur[sink], demand[sink]), shape='invhouse')
for source in sources:
    dot.node(source, "{:s}\n {:d}% @${:d}".format(source, sulfur[source], costs[source]))
for connection in connections:
    dot.edge(*connection)
dot

## Mathematical formulation

$N = \{ A, B, C, P, X, Y \}$ be the set of nodes in the graph, and let $\mathcal{A}$ be the set of arcs. We create two sets of variables:

* *flow* variables $x_{ij}$ for the arcs $(i,j) \in \mathcal{A}$, and
* *quality* (sulfur percentage) variables $y_i$ for the nodes $i \in N$.

For source nodes $i \in S := \{ A, B, C \}$, let $f_i$ be the fixed sulfur percentage and let $c_i$ be the unit cost for obtaining oil from that source. For sink nodes $i \in T := \{ X, Y \}$, let $u_i$ be the maximum sulfur percentage, let $p_i$ be the unit selling price, and let $d_i$ be the maximum demand. We can model this problem as follows:

&nbsp;
<span style='font-size: 12pt'>
$$ 
\begin{alignat*}{4}
\max_{x, y}\ && \sum_{i \in T} \sum_{(j,i) \in \mathcal{A}} p_i x_{ji} &- \sum_{i \in S} \sum_{(i,j) \in \mathcal{A}} c_i x_{ij} \\
\textrm{s.t. } && \sum_{(j,i) \in \mathcal{A}} x_{ji} &= \sum_{(i,j) \in \mathcal{A}} x_{ij} && \forall i \in N \setminus (S \cup T) \quad && \textrm{(flow balance)} \\
&& y_i \sum_{(j,i) \in \mathcal{A}} x_{ji} &= \sum_{(j,i) \in \mathcal{A}} y_j x_{ji} && \forall i \in N && \textrm{(define quality)} \\
&& y_i &= f_i && \forall i \in S \quad && \textrm{(fix source quality)} \\
&& y_i &\leq u_i && \forall i \in T && \textrm{(bound sink quality)} \\
&& \sum_{(j,i) \in \mathcal{A}} x_{ji} &\leq d_i && \forall i \in T && \textrm{(maximum demand)} \\
&& x, y &\geq 0
\end{alignat*}
$$
</span>

We can model this problem using `gurobipy`.

## Variables and bounds

In [ ]:
def define_variables(m):
    
    # Total flow per connection
    flow = m.addVars(connections, name="flow")

    # Quality (percentage of sulfur after blending all inflows)
    quality = m.addVars(sources + pools + sinks, name="quality")

    # Fix quality for all sources
    for source in sources:
        quality[source].LB = sulfur[source]
        quality[source].UB = sulfur[source]

    # Bound minimum quality for all sinks
    for sink in sinks:
        quality[sink].UB = max_sulfur[sink]
        
    return flow, quality

## Objective function (profit)

In [ ]:
def define_objective(m, flow, quality):
    
    # Build objective function
    total_costs = sum(costs[i] * flow[i,j] for s in sources for i,j in connections.select(s, '*'))
    total_revenue = sum(price[j] * flow[i,j] for t in sinks for i,j in connections.select('*', t))
    m.setObjective(total_revenue - total_costs, GRB.MAXIMIZE)

## Constraints

In [ ]:
def define_constraints(m, flow, quality):
    
    # Add balance constraints
    m.addConstrs((flow.sum('*', pool) == flow.sum(pool, '*') for pool in pools), name="balance")

    # Add demand constraints
    m.addConstrs((flow.sum('*', j) <= demand[j] for j in sinks), name="demand")

    # Add quality constraints
    m.addConstrs((quality[node] * flow.sum('*', node)
                  == sum(quality[i] * flow[i, j] for i,j in connections.select('*', node))
                  for node in pools + sinks), name="quality")

Now, we let Gurobi build and solve the model.

In [ ]:
m = Model()

flow, quality = define_variables(m)
define_objective(m, flow, quality)
define_constraints(m, flow, quality)

m.params.NonConvex=2
m.optimize()

## Visualize flows

In [ ]:
def draw_solution(m, flow, quality):
    
    dot = Digraph(graph_attr={'rankdir': 'LR'}, node_attr={'fontcolor':'blue', 'shape' : 'box'})
    for pool in pools: dot.node(pool, shape='doublecircle')
    for sink in sinks: dot.node(sink, label="<%s <br/>(%g)>" % (sink, sum([f.X for f in flow.select('*', sink)])),
                                      shape='invhouse')
    for connection in connections:
        dot.edge(*connection, label=("%g @ %g%%" % (flow[connection].X, quality[connection[0]].X)) if flow[connection].X > 0 else '', 
                              color='red' if flow[connection].X > 0 else 'lightgray',
                              fontname='courier', fontsize='10')
    return dot

draw_solution(m, flow, quality)

## Changing the data 

### Increasing demand

We increase the maximum demand of product X from 100 to 600 and solve the model again.

In [ ]:
demand['X'] = 600
m2 = Model()

flow2, quality2 = define_variables(m2)
define_objective(m2, flow2, quality2)
define_constraints(m2, flow2, quality2)

m2.params.NonConvex=2
m2.optimize()

In [ ]:
# Draw solution
draw_solution(m2, flow2, quality2)

### Changing source price

We lower the price of extracting crude oil from source B from $\$16$ to $\$13$.

In [ ]:
costs['B'] = 13

m3 = Model()

flow3, quality3 = define_variables(m3)
define_objective(m3, flow3, quality3)
define_constraints(m3, flow3, quality3)

m3.params.NonConvex=2
m3.optimize()

In [ ]:
# Draw solution
draw_solution(m3, flow3, quality3)